# Homology Modeling using MODELLER

In this lab, we will first look at a few structures of MPro. Then we will build a model of MPro from a bat coronavirus for which no structures are available.

The latter part of this lab was adapted to model MPro (instead of PETase) from [Lab 04 of IIBM3202 Molecular Modeling and Simulation](https://github.com/pb3lab/ibm3202/blob/master/tutorials/lab04_cm.ipynb) from the Institute for Biological and Engineering at Pontificia Universidad Catolica de Chile.

#Part 0 – Downloading and Installing the required software

Before we start, you must first **remember to start the hosted runtime in Google Colab**.

Then, we must install several pieces of software to perform this tutorial. Namely:
- **MODELLER**, a famous homology modelling software.
- **py3Dmol**, for visualization of the template and modelled protein structures.
- **prody**, for manipulation and retrieval of protein structures and sequences.

1. We will first install MODELLER as follows:

⚠️**WARNING!:** In order to use MODELLER, you will need to obtain an Academic License by registering **[in this website](https://salilab.org/modeller/registration.html)**. The license key will be immediately sent to your email address.

In [ ]:
#Before running this script, make sure to replace the MODELLER
#License Key with the one sent after registration in the MODELLER website
!wget https://salilab.org/modeller/10.1/modeller-10.1.tar.gz
#Then, we extract the downloaded folder containing MODELLER 10.1
!tar -zxf modeller-10.1.tar.gz
!echo "MODELLER extraction completed"
#Then, we switch onto the MODELLER folder
#with an automagic command
%cd modeller-10.1
#And we prepare a file containing the minimal setup elements
#For installing, including a license key
with open('modeller_config', 'a') as f:
  f.write("3\n")
  f.write("/content/compiled/MODELLER\n")
# --> ADD YOUR LICENSE KEY HERE!
  f.write("MODELIRANJE\n")
!./Install < modeller_config
!echo "MODELLER set up completed"
%cd /content/

--2022-02-28 19:36:00--  https://salilab.org/modeller/10.1/modeller-10.1.tar.gz
Resolving salilab.org (salilab.org)... 169.230.79.19
Connecting to salilab.org (salilab.org)|169.230.79.19|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 45026710 (43M) [application/x-gzip]
Saving to: ‘modeller-10.1.tar.gz’

modeller-10.1.tar.g 100%[===================>]  42.94M  24.9MB/s    in 1.7s    

2022-02-28 19:36:02 (24.9 MB/s) - ‘modeller-10.1.tar.gz’ saved [45026710/45026710]

MODELLER extraction completed
/content/modeller-10.1
Installation of MODELLER 10.1

This script will install MODELLER 10.1 into a specified directory
for which you have read/write permissions.

To accept the default answers indicated in [...], press <Enter> only.

------------------------------------------------------------------------

The currently supported architectures are as follows:

   1) Linux x86 PC (e.g. RedHat, SuSe).
   2) IBM AIX OS.
   3) x86_64 (Opteron/EM64T) box (Linux).
   4) Alt

In [ ]:
#Creating a symbolic link
%cd modeller-10.1
!ln -sf /content/compiled/MODELLER/bin/mod10.1 /usr/bin/
%cd /content/
#Checking if MODELLER works
!mod10.1 | awk 'NR==1{if($1=="usage:") print "MODELLER succesfully installed"; else if($1!="usage:") print "Something went wrong. Please install again"}'

/content/modeller-10.1
/content
MODELLER succesfully installed


2. Then, we will install prody

In [ ]:
try:
  import prody
except:
  !pip install -U prody
  import prody

     |████████████████████████████████| 11.9 MB 6.8 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 2.3 MB 25.9 MB/s 
  Created wheel for prody: filename=ProDy-2.0.2-cp37-cp37m-linux_x86_64.whl size=10816870 sha256=6a072c550707ec69a818d1e29a9c7120ae6eb80122331ec91dac7078ec7a5d5c
  Stored in directory: /root/.cache/pip/wheels/c4/d9/6f/f251b9e10fe631fe6430b92140944299feb0e7e036917e275a
Successfully built prody


3. Finally, we will install py3Dmol

In [ ]:
try:
  import py3Dmol
except:
  !pip install py3Dmol
  import py3Dmol

As we mentioned during the lecture, **structure space is rather small when compared with the sequence space**. In fact, hierarchical structure classifications such as **CATH** have demonstrated that only a few proteins of the enormous pool of structures being deposited each year in the Protein Data Bank are known to provide novel folds. In this regard, it seems that we have discovered almost all protein folds. Moreover, the elegant experiment by Chothia & Lesk [Chothia C & Lesk AM (1986) _EMBO J_ 5(4), 823–826] revealed that, generally, **protein structures are quite similar between proteins when their sequence identity is > 30-40%**, with some remarkable exceptions to this rule).

# Part I - Visualizing sequence-structure similarity

As an illustrative example of the fact that similar sequences often lead to similar structure, let's align and visualize crystal structures of MPro from the original SARS-CoV and SARS-CoV-2.

Firrst, we will use prody to superpose a structure of SARS-CoV-2 MPro onto a structure of SARS-CoV MPro.

In [ ]:
%cd /content/
%mkdir prody
%cd prody

/content
/content/prody


In [ ]:
PDB_1wof = prody.parsePDB('1wof')
PDB_5rh2 = prody.parsePDB('5rh2')

PDB_1wof_prot = PDB_1wof.select('protein')
PDB_5rh2p = PDB_5rh2.select('protein')

map_1wof_5rh2, map_5rh2_1wof, seqid, overlap = \
  prody.matchChains(PDB_1wof_prot, PDB_5rh2p)[0]
transformation = prody.calcTransformation(map_5rh2_1wof, map_1wof_5rh2)

prody.applyTransformation(transformation, PDB_5rh2)
prody.writePDB('5rh2_aligned.pdb', PDB_5rh2)
prody.writePDB('1wof.pdb', PDB_1wof)
prody.writePDB('1wofa.pdb', PDB_1wof.select('chain A'))

@> Connecting wwPDB FTP server RCSB PDB (USA).
@> 1wof downloaded (1wof.pdb.gz)
@> PDB download via FTP completed (1 downloaded, 0 failed).
@> 5051 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> Connecting wwPDB FTP server RCSB PDB (USA).
@> 5rh2 downloaded (5rh2.pdb.gz)
@> PDB download via FTP completed (1 downloaded, 0 failed).
@> 2651 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> Checking AtomGroup 1wof: 2 chains are identified
@> Checking AtomGroup 5rh2: 1 chains are identified
@> Trying to match chains based on residue numbers and names:
@>   Comparing Chain A from 1wof (len=309) and Chain A from 5rh2 (len=304):
@> 	Match: 304 residues match with 96% sequence identity and 98% overlap.
@>   Comparing Chain B from 1wof (len=304) and Chain A from 5rh2 (len=304):
@> 	Match: 302 residues match with 95% sequence identity and 99% overlap.
@> WARNING mobile is an AtomMap instance, consider assign weights=mobile.getFlags("mapped") if there are dummy atoms in mobile
@> WARN

'1wofa.pdb'

Next, let us visualize the secondary structure of the two proteins. What do you notice?

In [ ]:
view = py3Dmol.view()
view.setBackgroundColor('white')
view.addModel(open('1wofa.pdb', 'r').read(),'pdb')
view.addModel(open('5rh2_aligned.pdb', 'r').read(),'pdb')
view.setStyle({'model':0}, {'cartoon': {'color':'purple'}})
view.setStyle({'model':1}, {'cartoon': {'color':'yellow'}})
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Finally, compare side chain positions. How do they compare?

In [ ]:
view = py3Dmol.view()
view.setBackgroundColor('white')
view.addModel(open('1wofa.pdb', 'r').read(),'pdb')
view.addModel(open('5rh2_aligned.pdb', 'r').read(),'pdb')
view.setStyle({'and':[{'model':0},{'chain':'A'}]}, {'cartoon': {'color':'purple'}})
view.addStyle({'and':[{'model':0},{'chain':'A'}]}, {'stick': {'colorscheme':'purpleCarbon'}})
view.setStyle({'model':1}, {'cartoon': {'color':'yellow'}})
view.addStyle({'model':1}, {'stick': {'colorscheme':'yellowCarbon'}})
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

MPro is actually a dimer. For simility we have only shown one of the monomers so far. Now let's look more closely at the side chain positions. Do you notice any patterns with side chains variations 

* on the surface 
* in the interior of the protein
* at the interface between subunits?

In [ ]:
view = py3Dmol.view()
view.setBackgroundColor('white')
view.addModel(open('1wof.pdb', 'r').read(),'pdb')
view.addModel(open('5rh2_aligned.pdb', 'r').read(),'pdb')
view.setStyle({'and':[{'model':0},{'chain':'A'}]}, {'cartoon': {'color':'purple'}})
view.addStyle({'and':[{'model':0},{'chain':'A'}]}, {'stick': {'colorscheme':'purpleCarbon'}})
view.setStyle({'and':[{'model':0},{'chain':'B'}]}, {'cartoon': {'color':'grey'}})
view.setStyle({'model':1}, {'cartoon': {'color':'yellow'}})
view.addStyle({'model':1}, {'stick': {'colorscheme':'yellowCarbon'}})
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

# Part II - Template selection and sequence alignment

1. Let's move on to modeling the bat coronavirus MPro. The first step to structure prediction is to obtain the sequence that you want to model. We have obtained the amino acid sequence from [UniProt](https://www.uniprot.org/blast/?about=P0C6W6[3239-3544]&key=Chain&id=PRO_0000043082). Now lets store the sequence in a file.

In [ ]:
%cd /content/
%mkdir modeller
%cd modeller

/content
/content/modeller


In [ ]:
# sp|P0C6W6|3239-3544
F = open('target.fasta','w')
F.write(""">target
SGFRKMAFPSGKVEGCMVQVTCGTTTLNGLWLDDTVYCPRHVICTAEDMLNPNYEDLLIR
KSNHSFLVQAGNVQLRVIGHSMQNCLLRLKVDTSNPKTPKYKFVRIQPGQTFSVLACYNG
SPSGVYQCAMRPNHTIKGSFLNGSCGSVGFNIDYDCVSFCYMHHMELPTEVHAGTDLEGK
FYGPFVDRQTAQAAGTDTTITLNVLAWLYAAVINGDRWFLNRFTTTLNDFNLVAMKYNYE
PLTQDHVDILGPLSAQTGIAVLDMCAALKELLQNGMNGRTILGSTILEDEFTPFDVVRQC
SGVTFQ""")
F.close()

Selecting an appropriate template for modeling a structure of a homologous protein is as crucial as an appropriate alignment to correctly position the different residues.

**QUESTION:** What features of a crystal structure do you think are important for choosing the best template?

2. We will find the potential best templates from the whole PDB database to model the structure of our target protein using the **profile.build()** command from MODELLER.

  For this purpose, we need a text file containing a list of non-redundant PDB sequences at 95% sequence identity and an appropriate script for running MODELLER.

In [ ]:
#Downloading pdb_95.pir
!wget https://salilab.org/modeller/downloads/pdb_95.pir.gz
!gunzip pdb_95.pir.gz
#Downloading the build_profile.py script from GitHub
!wget https://raw.githubusercontent.com/pb3lab/ibm3202/master/scripts/build_profile.py

--2022-02-28 19:39:29--  https://salilab.org/modeller/downloads/pdb_95.pir.gz
Resolving salilab.org (salilab.org)... 169.230.79.19
Connecting to salilab.org (salilab.org)|169.230.79.19|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 17047044 (16M) [application/x-gzip]
Saving to: ‘pdb_95.pir.gz’

pdb_95.pir.gz       100%[===================>]  16.26M  18.6MB/s    in 0.9s    

2022-02-28 19:39:30 (18.6 MB/s) - ‘pdb_95.pir.gz’ saved [17047044/17047044]

--2022-02-28 19:39:31--  https://raw.githubusercontent.com/pb3lab/ibm3202/master/scripts/build_profile.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1321 (1.3K) [text/plain]
Saving to: ‘build_profile.py’

build_profile.py    100%[===================>]   1.29K  --.-KB/s    in 0s    

In [ ]:
#Running the build_profile script
!mod10.1 build_profile.py
#Printing only the list of potential templates
!sed -n '/HITS FOUND IN ITERATION:     1/,/Weight Matrix/p;/Weight Matrix/q' build_profile.log

'import site' failed; use -v for traceback
HITS FOUND IN ITERATION:     1


Dynamically allocated memory at     amaxprofile [B,KiB,MiB]:      1148189    1121.278     1.095
> 7c2yA                      1    4186   73900     289     306   95.50     0.0           2   289     4   297     1   289
> 1lvoA                      1    5581   30900     299     306   44.15     0.0           3   299     1   303     1   299
> 3ebnA                      1    6001   25950     100     306  100.00     0.0           4   100   198   297     1   100
> 2zu2A                      1    6205   29150     300     306   40.80     0.0           5   298     1   303     1   299
> 2ynaA                      1   18969   39300     306     306   50.98     0.0           6   302     1   306     1   306
> 4zroA                      1   21606   31450     299     306   44.15     0.0           7   299     1   303     1   299
> 5wkkA                      1   22578   40100     301     306   53.02     0.0           8   297     1

In this particular example, a BLOSUM62 similarity matrix is being used for determining the sequence identity between target and potential templates. Also, we are employing only one search iteration and the parameter max_aln_evalue is set to 0.01, indicating that only sequences with e-values smaller than or equal to 0.01 will be included in the final profile.

For simplicity, we just printed out the PDB table from the resulting log file generated during this analysis.

As you can see, several PDB files are indicated. The important columns to determine the best templates from this analysis are the fifth, seventh and eight columns, which correspond to the sequence length of the target protein, the sequence identity and the e-value, respectively.

**QUESTION:** From this analysis, which template would be better for modeling the structure of our target sequence?

In [ ]:
# --> Enter information for the template below
template_pdb = '7c2y'
template_chain = 'A'

# Downloads and decompresses
prody.parsePDB(template_pdb)
!gunzip {template_pdb}.pdb.gz

@> Connecting wwPDB FTP server RCSB PDB (USA).
@> 7c2y downloaded (7c2y.pdb.gz)
@> PDB download via FTP completed (1 downloaded, 0 failed).
@> 4383 atoms and 1 coordinate set(s) were parsed in 0.19s.


3. Now, we will **align the sequence of our template protein with the sequence of our target protein**, such that we can model the structure.

In [ ]:
F = open('align2D.py', 'w')
F.write(f"""from modeller import *

env = environ()
aln = alignment(env)
mdl = model(env, file='{template_pdb}', model_segment=('FIRST:{template_chain}','LAST:{template_chain}'))
aln.append_model(mdl, align_codes='{template_pdb}{template_chain}', atom_files='{template_pdb}.pdb')
aln.append(file='target.fasta', align_codes='target', alignment_format='FASTA')
aln.align2d()
aln.write(file='aligned.fasta', alignment_format='FASTA')
aln.write(file='aligned.ali', alignment_format='PIR')
aln.write(file='aligned.pap', alignment_format='PAP')
""")
F.close()

In [ ]:
!mod10.1 align2D.py

'import site' failed; use -v for traceback


4. You will end up with two new files (aligned.ali and aligned.fasta) that contain the pairwise alignment of the target and template sequences. Load the FASTA file into [Alignment Viewer 2.0](https://fast.alignmentviewer.org/). You can also use our Colab-mounted MSA viewer below:

In [ ]:
#@title Protein MSA Viewer in Google Colab
#The following code is modified from the wonderful viewer developed by Damien Farrell
#https://dmnfarrell.github.io/bioinformatics/bokeh-sequence-aligner

#Importing all modules first
import os, io, random
import string
import numpy as np

from Bio.Seq import Seq
from Bio.Align import MultipleSeqAlignment
from Bio import AlignIO, SeqIO

import panel as pn
import panel.widgets as pnw
pn.extension()

from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, Plot, Grid, Range1d
from bokeh.models.glyphs import Text, Rect
from bokeh.layouts import gridplot

#Setting up the amino color code according to Zappo color scheme
def get_colors(seqs):
    #make colors for bases in sequence
    text = [i for s in list(seqs) for i in s]
    #Use Zappo color scheme
    clrs =  {'K':'red',
             'R':'red',
             'H':'red',             
             'D':'green',
             'E':'green',
             'Q':'blue',
             'N':'blue',
             'S':'blue',
             'T':'blue',
             'A':'blue',
             'I':'blue',
             'L':'blue',
             'M':'blue',
             'V':'blue',
             'F':'orange',
             'Y':'orange',
             'W':'orange',
             'C':'blue',
             'P':'yellow',
             'G':'orange',
             '-':'white'}
    colors = [clrs[i] for i in text]
    return colors

#Setting up the MSA viewer
def view_alignment(aln, fontsize="9pt", plot_width=800):
    """Bokeh sequence alignment view"""

    #make sequence and id lists from the aln object
    seqs = [rec.seq for rec in (aln)]
    ids = [rec.id for rec in aln]    
    text = [i for s in list(seqs) for i in s]
    colors = get_colors(seqs)    
    N = len(seqs[0])
    S = len(seqs)    
    width = .4

    x = np.arange(1,N+1)
    y = np.arange(0,S,1)
    #creates a 2D grid of coords from the 1D arrays
    xx, yy = np.meshgrid(x, y)
    #flattens the arrays
    gx = xx.ravel()
    gy = yy.flatten()
    #use recty for rect coords with an offset
    recty = gy+.5
    h= 1/S
    #now we can create the ColumnDataSource with all the arrays
    source = ColumnDataSource(dict(x=gx, y=gy, recty=recty, text=text, colors=colors))
    plot_height = len(seqs)*15+50
    x_range = Range1d(0,N+1, bounds='auto')
    if N>100:
        viewlen=100
    else:
        viewlen=N
    #view_range is for the close up view
    view_range = (0,viewlen)
    tools="xpan, xwheel_zoom, reset, save"

    #entire sequence view (no text, with zoom)
    p = figure(title=None, plot_width= plot_width, plot_height=50,
               x_range=x_range, y_range=(0,S), tools=tools,
               min_border=0, toolbar_location='below')
    rects = Rect(x="x", y="recty",  width=1, height=1, fill_color="colors",
                 line_color=None, fill_alpha=0.6)
    p.add_glyph(source, rects)
    p.yaxis.visible = False
    p.grid.visible = False  

    #sequence text view with ability to scroll along x axis
    p1 = figure(title=None, plot_width=plot_width, plot_height=plot_height,
                x_range=view_range, y_range=ids, tools="xpan,reset",
                min_border=0, toolbar_location='below')#, lod_factor=1)          
    glyph = Text(x="x", y="y", text="text", text_align='center',text_color="black",
                text_font="monospace",text_font_size=fontsize)
    rects = Rect(x="x", y="recty",  width=1, height=1, fill_color="colors",
                line_color=None, fill_alpha=0.4)
    p1.add_glyph(source, glyph)
    p1.add_glyph(source, rects)

    p1.grid.visible = False
    p1.xaxis.major_label_text_font_style = "bold"
    p1.yaxis.minor_tick_line_width = 0
    p1.yaxis.major_tick_line_width = 0

    p = gridplot([[p],[p1]], toolbar_location='below')
    return p

#Loading the viewer by indicating the MSA file and format to read
#@markdown Name of the MSA file (including the filetype)
MSAfile = 'aligned.fasta' #@param {type:"string"}
MSAformat = 'fasta' #@param {type:"string"}
aln = AlignIO.read(MSAfile,MSAformat)
p = view_alignment(aln, plot_width=900)
pn.pane.Bokeh(p)

Bokeh(Column)

# Part III - Generate and visualize a comparative model using MODELLER

1. Once your target and template sequences are aligned, use the **model-single.py** script for finally obtaining a structure of your target through comparative modeling. Again, read the script and check how the sequences and structures are called in MODELLER through these scripts. In this case, we are also performing this step on a separate folder.

  Please note that 1 model is not enough, as there is an energy function defining the optimal position of atomic coordinates, thus different models will have different energies. Generally, between 50-100 are generated for sufficient evaluation.

**💡 HINT:** For our example, the generation of 50 models takes around 15 min on Google Colab, whereas 10 models are generated in about 3 min. You can edit the number of models to generate on the `model-single.py` script.

In [ ]:
%cd /content/
%mkdir modeller
%cd modeller

In [ ]:
F = open('model-single.py', 'w')

F.write(f"""from modeller import *
from modeller.automodel import *
#from modeller import soap_protein_od

env = environ()
a = automodel(env, alnfile='aligned.ali',
              knowns='{template_pdb}{template_chain}', sequence='target',
              assess_methods=(assess.DOPE,
                              #soap_protein_od.Scorer(),
                              assess.GA341))
a.starting_model = 1
a.ending_model = 50
a.make()

# Get a list of all successfully built models from a.outputs
ok_models = filter(lambda x: x['failure'] is None, a.outputs)

# Rank the models by DOPE score
key = 'DOPE score'
ok_models.sort(lambda a,b: cmp(a[key], b[key]))

# Get top model
m = ok_models[0]
print "Top model: %s (DOPE score %.3f)" % (m['name'], m[key])
""")
F.close()

In [ ]:
#Running the model-single script
!mod10.1 model-single.py

'import site' failed; use -v for traceback


In [ ]:
# Shows the end of the log file, which includes the best model
!tail model-single.log

Filename                          molpdf     DOPE score    GA341 score
----------------------------------------------------------------------
target.B99990001.pdb          1547.65906   -34681.78125        1.00000
target.B99990002.pdb          1624.41858   -34730.73828        1.00000
target.B99990003.pdb          1471.36133   -35116.42188        1.00000
target.B99990004.pdb          1650.42896   -34899.98828        1.00000
target.B99990005.pdb          1527.14697   -35030.04688        1.00000

Top model: target.B99990003.pdb (DOPE score -35116.422)
Total CPU time [seconds]                                 :      96.31


2. The output from this process is a bunch of PDB files, each one of them corresponding to a comparative model of our target protein, that are numbered from 1 up to the total number of models requested during comparative modeling.

  Also, the **model-single.log** output has the total potential energy for each structure,according to MODELLER’s DOPE (discrete optimized protein energy) score. For simplicity, this script was modified to indicate the model with the best DOPE score. We will be working only with the model with the best score for the remainder of the session.
  
  As an example, our best model during preparation of this tutorial showed the following DOPE score:

```
Top model: target.B99990021.pdb (DOPE score -35317.168)
Total CPU time [seconds]                                 :     885.31
```

3. Before we check the quality of our model, we will take a look at it on **py3Dmol**.

**💡 HINT:** We are creating a copy of our model and changing the chain id, to make it easier to load both structures into py3Dmol.

In [ ]:
# --> Modify this for your best model and chain
# Copying our best model with a new chain id
!sed "s/ A / B /g" target.B99990003.pdb > bestmodel.pdb

In [ ]:
#Setting up py3Dmol for visualization
view=py3Dmol.view()
#Loading template
view.addModel(open(f'{template_pdb}.pdb', 'r').read(),'pdb')
#Loading best DOPE score model
view.addModel(open('bestmodel.pdb', 'r').read(),'pdb')
#Coloring the structures by chain id
view.setStyle({'model':0}, {'cartoon': {'color':'purple'}})
view.setStyle({'model':1}, {'cartoon': {'color':'yellow'}})
view.zoomTo()
view.setBackgroundColor('white')
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

4. Finally, to check the stereochemical quality of the model and its comparison to experimentally solved structures, we will use the [SAVES server](https://saves.mbi.ucla.edu), which employs several structure-based scoring strategies:

* **VERIFY3D** (i.e. compatibility of an atomic 3D model to its 1D sequence when compared tothe energetics of good structures from the PDB).
* **ERRAT** (i.e. quality of non-bonded interactions of a region when compared to similar regions from highly refined structures).
* **PROCHECK** (stereochemical and geometrical quality of the model, via Ramachandran plots, sidechain rotamers, etc).

5. Download your best model, upload it to SAVES and wait for the results. Briefly:
- **Check the VERIFY3D results:** >80% of the residues should have an average score ≥ 0.2, whereas the score profile allows you to identify conflicting regions.
- **Check the Ramachandran plot:** Are there any residues outside the allowed regions? What types of residues are found within those regions? (Check it by clicking on each dot in the plot)
- **Check the errors in PROCHECK:** are the errors located within the loop regions?



<figure>
<center>
<img src='https://raw.githubusercontent.com/pb3lab/ibm3202/master/images/cm_04.png'/>
</center>
</figure>

[This article](https://journals.plos.org/ploscompbiol/article?id=10.1371/journal.pcbi.1007449) contains more recommendations on comparative modelling of protein structures.

# Part IV - Modeling a complete dimer

In Part III, we built a model of a single subunit of MPro. In this part, we will build a model of the dimer by aligning two copies of the monomer to the template structure.

In [ ]:
%cd /content/
%mkdir modeller
%cd modeller

/content
mkdir: cannot create directory ‘modeller’: File exists
/content/modeller


First, we align the model to each chain from the template.

In [ ]:
PDB_model = prody.parsePDB('bestmodel.pdb')
PDB_template = prody.parsePDB(f'{template_pdb}.pdb')

PDB_model_prot = PDB_model.select('protein')
PDB_model_template = PDB_template.select('protein')

matches = \
  prody.matchChains(PDB_model_prot, PDB_model_template)

for match in matches:
  map_model_template, map_template_model, seqid, overlap = match
  chain = map_template_model.getChids()[0]
  transformation = prody.calcTransformation(map_model_template, map_template_model)
  inv_transformation = prody.calcTransformation(map_template_model, map_model_template)
  PDB_model.setChids([chain for i in range(len(PDB_model.getChids()))])
  prody.applyTransformation(transformation, PDB_model)
  prody.writePDB(f'bestmodel_aligned_to_{template_pdb}{chain}.pdb', PDB_model)
  prody.applyTransformation(inv_transformation, PDB_model)

@> 2376 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4383 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> Checking AtomGroup bestmodel: 1 chains are identified
@> Checking AtomGroup 7c2y: 2 chains are identified
@> Trying to match chains based on residue numbers and names:
@>   Comparing Chain A from bestmodel (len=306) and Chain A from 7c2y (len=289):
@> 	Match: 289 residues match with 96% sequence identity and 94% overlap.
@>   Comparing Chain A from bestmodel (len=306) and Chain B from 7c2y (len=283):
@> 	Match: 283 residues match with 96% sequence identity and 92% overlap.
@> WARNING mobile is an AtomMap instance, consider assign weights=mobile.getFlags("mapped") if there are dummy atoms in mobile
@> WARNING target is an AtomMap instance, consider assign weights=target.getFlags("mapped") if there are dummy atoms in target
@> WARNING mobile is an AtomMap instance, consider assign weights=mobile.getFlags("mapped") if there are dummy atoms in mobile
@> WARNING target 

Next, we join the files together.

In [ ]:
dat = ''
for chain in ['A','B']:
  with open(f'bestmodel_aligned_to_{template_pdb}{chain}.pdb', 'r') as F:
    dat += F.read()
with open(f'bestmodel_aligned.pdb', 'w') as F:
  F.write(dat)

Finally, we visualize the model and the template.

In [ ]:
#Setting up py3Dmol for visualization
view=py3Dmol.view()
#Loading template
view.addModel(open(f'{template_pdb}.pdb', 'r').read(),'pdb')
view.addModel(open(f'bestmodel_aligned.pdb', 'r').read(),'pdb')
#Coloring the structures by model id
view.setStyle({'model':0}, {'cartoon': {'color':'purple'}})
view.setStyle({'model':1}, {'cartoon': {'color':'yellow'}})
view.zoomTo()
view.setBackgroundColor('white')
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

# Part IV. Saving the model

We will use `bestmodel_aligned.pdb` in future labs. The code below will store it on your Google Drive.

In [4]:
# Mounts your Google Drive
from google.colab import drive
if not os.path.isdir('/content/drive'):
  drive.mount('/content/drive')

# Use GitHub to clones or updates the workshop repository
GitHub_dir = '/content/drive/MyDrive/GitHub'
import os
if not os.path.isdir(GitHub_dir):
  !mkdir -p {GitHub_dir}

os.chdir(GitHub_dir)
if not os.path.isdir(os.path.join(GitHub_dir,'modelingworkshop')):
  !git clone https://github.com/CCBatIIT/modelingworkshop
else:
  os.chdir(os.path.join(GitHub_dir,'modelingworkshop'))
  !git pull origin main

# Copies bestmodel_aligned to Google Drive
!cp /content/modeller/bestmodel_aligned.pdb /content/drive/MyDrive/GitHub/modelingworkshop/labs-complete/1-2/

From https://github.com/CCBatIIT/modelingworkshop
 * branch            main       -> FETCH_HEAD
Already up to date.


**This is the end of the fourth tutorial! Good Science!!**